In [3]:
import numpy as np
import librosa
import librosa.display
from IPython.display import Audio
import cv2
import matplotlib.pyplot as plt

In [15]:
from PIL import Image
import glob
import os

for root, subfolder, filenames in os.walk("./reconstructed_images"):
    for i, file in enumerate(filenames):
        img = Image.open(f"./reconstructed_images/{file}")
        box = (200,180,1328,1328)
        img2 = img.crop(box)
        img2.save(f"img_crop_{i}.png")


KeyboardInterrupt: 

In [4]:
# Load the spectrogram image using OpenCV
n_fft = 512
hop_length = 16
sr=24000

def reconstruct_audio(image):
    spec_image = cv2.imread(image, cv2.IMREAD_GRAYSCALE)
    
    # Convert the spectrogram image to a numpy array
    spec_array = np.array(spec_image)
        
    # Denormalise Spectrogram
    spec_array = cv2.normalize(spec_array, None, alpha=0, beta=255, norm_type=cv2.NORM_MINMAX) #Produces cleaner audio although a lot of frequency content is lost

    # Convert the spectrogram array to a magnitude spectrogram
    spec = librosa.db_to_amplitude(spec_array) 
        
    # Reconstruct the audio signal from the magnitude spectrogram
    y_reconstructed = librosa.feature.inverse.mel_to_audio(spec, sr=sr, n_fft=n_fft, n_iter=1, fmax=sr, hop_length=hop_length)
    
    #return y_reconstructed
    # Save the reconstructed audio signal as a WAV file
    return Audio(y_reconstructed, rate=sr)


In [37]:
reconstruct_audio('image (100).png')

In [5]:
import scipy.io.wavfile as wavefile

In [7]:
from PIL import Image
import glob
import os
import re
# Set the path to the folder containing the images
image_folder = './Cropped Images/'
# Set the name of the output GIF file
output_folder = "./output/"

# Get a list of all the image file names in the folder
image_files = glob.glob(image_folder + '*.png')
# Sort the file names alphabetically to ensure they are in the correct order

image_files.sort(key=lambda f: int(re.sub('\D', '', f)))
#image_files.sort(key=os.path.getmtime)
def create_final_audio(folder):
    
        audio = np.array([])
        for i, filename in enumerate(image_files):
            spec_image = cv2.imread(filename, cv2.IMREAD_GRAYSCALE)
        
            spec_array = np.array(spec_image)
 
            spec = librosa.db_to_amplitude(spec_array) 
      
            y_reconstructed = librosa.feature.inverse.mel_to_audio(spec, sr=sr, n_fft=n_fft, n_iter=1, fmax=sr, hop_length=hop_length)
            
          
            audio = np.append(audio, y_reconstructed)
        return audio

       


In [8]:
final_array = create_final_audio(image_files)

C:\Users\kongf\anaconda3\lib\site-packages\librosa\util\decorators.py:88: UserWarning: Empty filters detected in mel frequency basis. Some channels will produce empty responses. Try increasing your sampling rate (and fmax) or reducing n_mels.
  return f(*args, **kwargs)


In [9]:
Audio(final_array, rate=sr)